In [1]:
import os
os.getcwd()

'C:\\Users\\janmi\\PycharmProjects\\Magisterka'

Pierwsza próba zapisania adnotacji do zdjęć w jsonnie i ustawinie tylko kategori "car"

In [7]:
import os
import json
import cv2
from glob import glob

def yolo_to_coco(yolo_dir, img_dir, output_file):
    annotations = []
    images = []
    categories = [{'id': 1, 'name': 'car'}]
    annotation_id = 0

    for img_path in glob(os.path.join(img_dir, '*.png')):
        img = cv2.imread(img_path)
        height, width, _ = img.shape
        img_id = os.path.splitext(os.path.basename(img_path))[0]

        images.append({
            'id': img_id,
            'file_name': os.path.basename(img_path),
            'height': height,
            'width': width
        })

        yolo_file = os.path.join(yolo_dir, img_id + '.txt')
        if os.path.exists(yolo_file):
            with open(yolo_file, 'r') as f:
                for line in f:
                    class_id, x_center, y_center, w, h = map(float, line.strip().split())
                    x_center *= width
                    y_center *= height
                    w *= width
                    h *= height
                    x = x_center - w / 2
                    y = y_center - h / 2

                    annotations.append({
                        'id': annotation_id,
                        'image_id': img_id,
                        'category_id': int(class_id) + 1,
                        'bbox': [x, y, w, h],
                        'area': w * h,
                        'iscrowd': 0
                    })
                    annotation_id += 1

    coco_format = {
        'images': images,
        'annotations': annotations,
        'categories': categories
    }

    with open(output_file, 'w') as f:
        json.dump(coco_format, f, indent=4)

# Paths
yolo_dir = r'C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\yolo_dir'
img_dir = r'C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\train'
output_file = r'C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\annotations.json'

# Convert YOLO to COCO format
yolo_to_coco(yolo_dir, img_dir, output_file)

print(f"COCO annotations saved to {output_file}")


COCO annotations saved to C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\annotations.json


Przeiterowanie klasy by zgadzała się z oznaczeniami

In [12]:
import os
from glob import glob

def correct_annotations(annotation_dir):
    for annotation_file in glob(os.path.join(annotation_dir, '*.txt')):
        with open(annotation_file, 'r') as file:
            lines = file.readlines()
        
        corrected_lines = []
        for line in lines:
            parts = line.strip().split()
            try:
                class_id = int(parts[0])
                if class_id > 0:
                    print(f"Correcting class_id {class_id} to 0 in file {annotation_file}")
                    parts[0] = '0'
                corrected_lines.append(' '.join(parts))
            except ValueError:
                print(f"Skipping invalid annotation in file {annotation_file}: {line.strip()}")
                continue
        
        with open(annotation_file, 'w') as file:
            file.write('\n'.join(corrected_lines))

# Paths to your annotation directories
train_annotation_dir = r'C:\Users\janmi\PycharmProjects\Magisterka\yolov5\labels\train'
val_annotation_dir = r'C:\Users\janmi\PycharmProjects\Magisterka\yolov5\labels\val'

# Correct annotations
correct_annotations(train_annotation_dir)
correct_annotations(val_annotation_dir)

print("Annotations corrected.")


Skipping invalid annotation in file C:\Users\janmi\PycharmProjects\Magisterka\yolov5\labels\train\classes.txt: dog
Skipping invalid annotation in file C:\Users\janmi\PycharmProjects\Magisterka\yolov5\labels\train\classes.txt: person
Skipping invalid annotation in file C:\Users\janmi\PycharmProjects\Magisterka\yolov5\labels\train\classes.txt: cat
Skipping invalid annotation in file C:\Users\janmi\PycharmProjects\Magisterka\yolov5\labels\train\classes.txt: tv
Skipping invalid annotation in file C:\Users\janmi\PycharmProjects\Magisterka\yolov5\labels\train\classes.txt: car
Skipping invalid annotation in file C:\Users\janmi\PycharmProjects\Magisterka\yolov5\labels\train\classes.txt: meatballs
Skipping invalid annotation in file C:\Users\janmi\PycharmProjects\Magisterka\yolov5\labels\train\classes.txt: marinara sauce
Skipping invalid annotation in file C:\Users\janmi\PycharmProjects\Magisterka\yolov5\labels\train\classes.txt: tomato soup
Skipping invalid annotation in file C:\Users\janmi\Py

Wytrenowanie modelu dla średniego gotowego modelu "yolov5m.pt"

In [14]:
!python C:\Users\janmi\PycharmProjects\Magisterka\yolov5\train.py --img 640 --batch 16 --epochs 100 --data C:\Users\janmi\PycharmProjects\Magisterka\yolov5\car_dataset.yaml --weights C:\Users\janmi\PycharmProjects\Magisterka\yolov5\yolov5m.pt

train: weights=C:\Users\janmi\PycharmProjects\Magisterka\yolov5\yolov5m.pt, cfg=, data=C:\Users\janmi\PycharmProjects\Magisterka\yolov5\car_dataset.yaml, hyp=yolov5\data\hyps\hyp.scratch-low.yaml, epochs=100, batch_size=16, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, evolve_population=yolov5\data\hyps, resume_evolve=None, bucket=, cache=None, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=yolov5\runs\train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=100, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest, ndjson_console=False, ndjson_file=False
github: up to date with https://github.com/ultralytics/yolov5 
YOLOv5  v7.0-331-gab364c98 Python-3.12.4 torch-2.3.1+cpu CPU

hyperparameters: lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005,

Sprawdzenie wytrenowanego modelu na danych testowych.

In [15]:
!python C:\Users\janmi\PycharmProjects\Magisterka\yolov5\detect.py --weights C:\Users\janmi\PycharmProjects\Magisterka\yolov5\runs\train\exp3\weights\best.pt --img 640 --conf 0.25 --source C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\test


detect: weights=['C:\\Users\\janmi\\PycharmProjects\\Magisterka\\yolov5\\runs\\train\\exp3\\weights\\best.pt'], source=C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\test, data=yolov5\data\coco128.yaml, imgsz=[640, 640], conf_thres=0.25, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=False, save_csv=False, save_conf=False, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=yolov5\runs\detect, name=exp, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False, vid_stride=1
YOLOv5  v7.0-331-gab364c98 Python-3.12.4 torch-2.3.1+cpu CPU

Fusing layers... 
Model summary: 212 layers, 20852934 parameters, 0 gradients, 47.9 GFLOPs
image 1/487 C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\test\0000000000.png: 256x640 1 car, 81.9ms
image 2/487 C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\test\0000000001.png: 256x640 1 car, 73.4ms
image 3/487 C:\User

Połączenie zdjęc z różnych datasetów, ustawienie indeksów oraz wykonanie resizingu aby każde zdjęcie miało takie same parametry

In [23]:
import os

# Path to the directory containing the images
directory = r'C:\Users\janmi\OneDrive\Pulpit\train\S00383'

# Starting index
start_index = 1241

# Get a list of all files in the directory
files = sorted(os.listdir(directory))

# Check if the number of files is correct
for idx, filename in enumerate(files):
    # Construct the new filename with 10 digits
    new_filename = f"{start_index + idx:010d}.jpg"
    
    # Get the full path of the old and new filenames
    old_file = os.path.join(directory, filename)
    new_file = os.path.join(directory, new_filename)
    
    # Rename the file
    os.rename(old_file, new_file)
print("File renaming completed successfully.")

File renaming completed successfully.


In [27]:
import os
from PIL import Image

# Path to the directory containing the images
directory = r'C:\Users\janmi\OneDrive\Pulpit\val\all'

# Desired size
new_size = (1392, 512)

# Starting index for renaming
start_index = 194

# Get a list of all files in the directory
files = sorted(os.listdir(directory))

# Check if the number of files is correct
for idx, filename in enumerate(files):
    # Full path to the original file
    old_file = os.path.join(directory, filename)
    
    # Check if the file is a jpg
    if filename.lower().endswith('.jpg'):
        # Open the image
        with Image.open(old_file) as img:
            # Resize the image
            img = img.resize(new_size, Image.LANCZOS)
            
            # Construct the new filename with 10 digits and .png extension
            new_filename = f"{start_index + idx:010d}.png"
            
            # Full path to the new file
            new_file = os.path.join(directory, new_filename)
            
            # Save the image as PNG
            img.save(new_file, 'PNG')
            
print("Image resizing and format conversion completed successfully.")


Image resizing and format conversion completed successfully.


Sprawdzenie czy jest ciągłość w nazwach labels

In [6]:
import os

# Path to the directory containing the images
directory = r'C:\Users\janmi\PycharmProjects\Magisterka\yolov5\labels\train'

# Expected range of filenames
start_index = 0
end_index = 1424

# Get a set of all filenames in the directory
files = set(os.listdir(directory))

# Check for missing filenames
missing_files = []
for i in range(start_index, end_index + 1):
    filename = f"{i:010d}.txt"  # Change the extension if needed
    if filename not in files:
        missing_files.append(filename)

if missing_files:
    print("Missing files:")
    for file in missing_files:
        print(file)
else:
    print("All filenames are continuous and accounted for.")


All filenames are continuous and accounted for.


In [30]:
import os

# Path to the directory containing the images
directory = r'C:\Users\janmi\PycharmProjects\Magisterka\yolov5\labels\train'

# Expected range of filenames
start_index = 0
end_index = 945

# Get a set of all filenames in the directory
files = set(os.listdir(directory))

# Check for missing filenames
missing_files = []
for i in range(start_index, end_index + 1):
    filename = f"{i:010d}.txt"  # Change the extension if needed
    if filename not in files:
        missing_files.append(filename)

if missing_files:
    print("Missing files:")
    for file in missing_files:
        print(file)
else:
    print("All filenames are continuous and accounted for.")


All filenames are continuous and accounted for.


Zaimportowanie torch dla szybszego trenowania i ponowne wytrenowanie dla modelu yolov5m.pt

In [1]:
import torch
print(torch.cuda.is_available())
print(torch.cuda.current_device())
print(torch.cuda.get_device_name(0))

True
0
NVIDIA GeForce RTX 4060 Ti


In [3]:
!python C:\Users\janmi\PycharmProjects\Magisterka\yolov5\train.py --img 640 --batch 16 --epochs 100 --data C:\Users\janmi\PycharmProjects\Magisterka\yolov5\car_dataset.yaml --weights C:\Users\janmi\PycharmProjects\Magisterka\yolov5\yolov5m.pt

train: weights=C:\Users\janmi\PycharmProjects\Magisterka\yolov5\yolov5m.pt, cfg=, data=C:\Users\janmi\PycharmProjects\Magisterka\yolov5\car_dataset.yaml, hyp=yolov5\data\hyps\hyp.scratch-low.yaml, epochs=100, batch_size=16, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, evolve_population=yolov5\data\hyps, resume_evolve=None, bucket=, cache=None, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=yolov5\runs\train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=100, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest, ndjson_console=False, ndjson_file=False
github:  YOLOv5 is out of date by 3 commits. Use 'git pull' or 'git clone https://github.com/ultralytics/yolov5' to update.
YOLOv5  v7.0-331-gab364c98 Python-3.12.4 torch-2.3.1+cu121 CUDA:0 (NVIDIA 

Dodanie większej ilości danych i ponowne przeprowadzenie sprawdzenia numerowania i parametrów zdjęć

In [4]:
import os

# Path to the directory containing the images
directory = r'C:\Users\janmi\OneDrive\Pulpit\test\S00044'

# Starting index
start_index = 487

# Get a list of all files in the directory
files = sorted(os.listdir(directory))

# Check if the number of files is correct
for idx, filename in enumerate(files):
    # Construct the new filename with 10 digits
    new_filename = f"{start_index + idx:010d}.jpg"
    
    # Get the full path of the old and new filenames
    old_file = os.path.join(directory, filename)
    new_file = os.path.join(directory, new_filename)
    
    # Rename the file
    os.rename(old_file, new_file)
print("File renaming completed successfully.")

File renaming completed successfully.


In [5]:
import os
from PIL import Image

# Path to the directory containing the images
directory = r'C:\Users\janmi\OneDrive\Pulpit\test\S00044'

# Desired size
new_size = (1392, 512)

# Starting index for renaming
start_index = 487

# Get a list of all files in the directory
files = sorted(os.listdir(directory))

# Check if the number of files is correct
for idx, filename in enumerate(files):
    # Full path to the original file
    old_file = os.path.join(directory, filename)
    
    # Check if the file is a jpg
    if filename.lower().endswith('.jpg'):
        # Open the image
        with Image.open(old_file) as img:
            # Resize the image
            img = img.resize(new_size, Image.LANCZOS)
            
            # Construct the new filename with 10 digits and .png extension
            new_filename = f"{start_index + idx:010d}.png"
            
            # Full path to the new file
            new_file = os.path.join(directory, new_filename)
            
            # Save the image as PNG
            img.save(new_file, 'PNG')
            
print("Image resizing and format conversion completed successfully.")


Image resizing and format conversion completed successfully.


In [6]:
!python C:\Users\janmi\PycharmProjects\Magisterka\yolov5\detect.py --weights C:\Users\janmi\PycharmProjects\Magisterka\yolov5\runs\train\exp4\weights\best.pt --img 640 --conf 0.25 --source C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\test

detect: weights=['C:\\Users\\janmi\\PycharmProjects\\Magisterka\\yolov5\\runs\\train\\exp4\\weights\\best.pt'], source=C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\test, data=yolov5\data\coco128.yaml, imgsz=[640, 640], conf_thres=0.25, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=False, save_csv=False, save_conf=False, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=yolov5\runs\detect, name=exp, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False, vid_stride=1
YOLOv5  v7.0-331-gab364c98 Python-3.12.4 torch-2.3.1+cu121 CUDA:0 (NVIDIA GeForce RTX 4060 Ti, 8188MiB)

Fusing layers... 
Model summary: 212 layers, 20852934 parameters, 0 gradients, 47.9 GFLOPs
image 1/634 C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\test\0000000000.png: 256x640 1 car, 51.1ms
image 2/634 C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\test\0000000001.png

In [11]:
import os

# Path to the directory containing the images
directory = r'C:\Users\janmi\PycharmProjects\Magisterka\yolov5\labels\val'

# Expected range of filenames
start_index = 0
end_index = 945

# Get a set of all filenames in the directory
files = set(os.listdir(directory))

# Check for missing filenames
missing_files = []
for i in range(start_index, end_index + 1):
    filename = f"{i:010d}.txt"  # Change the extension if needed
    if filename not in files:
        missing_files.append(filename)

if missing_files:
    print("Missing files:")
    for file in missing_files:
        print(file)
else:
    print("All filenames are continuous and accounted for.")

All filenames are continuous and accounted for.


In [12]:
#@title Select YOLOv5 🚀 logger {run: 'auto'}
logger = 'Comet' #@param ['Comet', 'ClearML', 'TensorBoard']

if logger == 'Comet':
  %pip install -q comet_ml
  import comet_ml; comet_ml.init()
elif logger == 'ClearML':
  %pip install -q clearml
  import clearml; clearml.browser_login()
elif logger == 'TensorBoard':
  %load_ext tensorboard
  %tensorboard --logdir runs/train

Note: you may need to restart the kernel to use updated packages.


Dla gotowych już danych wytrenowanie modelu dla uzywając gotowego już największego z dostępnych yolov5x.pt.

In [13]:
!python C:\Users\janmi\PycharmProjects\Magisterka\yolov5\train.py --img 640 --batch 16 --epochs 100 --data C:\Users\janmi\PycharmProjects\Magisterka\yolov5\car_dataset.yaml --weights C:\Users\janmi\PycharmProjects\Magisterka\yolov5\yolov5x.pt

Using device: cuda:0


train: weights=C:\Users\janmi\PycharmProjects\Magisterka\yolov5\yolov5x.pt, cfg=, data=C:\Users\janmi\PycharmProjects\Magisterka\yolov5\car_dataset.yaml, hyp=yolov5\data\hyps\hyp.scratch-low.yaml, epochs=100, batch_size=16, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, evolve_population=yolov5\data\hyps, resume_evolve=None, bucket=, cache=None, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=yolov5\runs\train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=100, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest, ndjson_console=False, ndjson_file=False
github:  YOLOv5 is out of date by 3 commits. Use 'git pull' or 'git clone https://github.com/ultralytics/yolov5' to update.
YOLOv5  v7.0-331-gab364c98 Python-3.12.4 torch-2.3.1+cu121 CUDA:0 (NVIDIA 

In [14]:
!python C:\Users\janmi\PycharmProjects\Magisterka\yolov5\detect.py --weights C:\Users\janmi\PycharmProjects\Magisterka\yolov5\runs\train\exp4\weights\best.pt --img 640 --conf 0.25 --source C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\test

detect: weights=['C:\\Users\\janmi\\PycharmProjects\\Magisterka\\yolov5\\runs\\train\\exp4\\weights\\best.pt'], source=C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\test, data=yolov5\data\coco128.yaml, imgsz=[640, 640], conf_thres=0.25, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=False, save_csv=False, save_conf=False, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=yolov5\runs\detect, name=exp, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False, vid_stride=1
YOLOv5  v7.0-331-gab364c98 Python-3.12.4 torch-2.3.1+cu121 CUDA:0 (NVIDIA GeForce RTX 4060 Ti, 8188MiB)

Fusing layers... 
Model summary: 212 layers, 20852934 parameters, 0 gradients, 47.9 GFLOPs
image 1/634 C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\test\0000000000.png: 256x640 1 car, 44.1ms
image 2/634 C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\test\0000000001.png

Podsumowanie w comet-mlu

https://www.comet.com/torekas/yolov5/de6f24212b2d400484835dd72b2c7b12?compareXAxis=step&experiment-tab=panels&showOutliers=true&smoothing=0&xAxis=step
key = de6f24212

In [6]:
import os

# Path to the directory containing the images
directory = r'C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\new\annotations'

# Expected range of filenames
start_index = 0
end_index = 1424

# Get a set of all filenames in the directory
files = set(os.listdir(directory))

# Check for missing filenames
missing_files = []
for i in range(start_index, end_index + 1):
    filename = f"{i:010d}.json"  # Change the extension if needed
    if filename not in files:
        missing_files.append(filename)

if missing_files:
    print("Missing files:")
    for file in missing_files:
        print(file)
else:
    print("All filenames are continuous and accounted for.")

All filenames are continuous and accounted for.


Skrypt konwertujący annotations z programu labaleme z formatu json na txt yolo

In [4]:
import json
import os

def labelme_to_yolo(labelme_path, output_path, classes):
    """
    Converts Labelme JSON annotations with polygons to YOLO format by finding bounding boxes.
    
    Args:
    - labelme_path: Path to the folder containing Labelme JSON files.
    - output_path: Path to save YOLO annotation files.
    - classes: List of class names (order matters for class ID).
    """
    if not os.path.exists(output_path):
        os.makedirs(output_path)

    for filename in os.listdir(labelme_path):
        if filename.endswith(".json"):
            json_path = os.path.join(labelme_path, filename)
            with open(json_path, 'r') as file:
                data = json.load(file)
                
                image_width = data['imageWidth']
                image_height = data['imageHeight']
                yolo_annotations = []
                
                for shape in data['shapes']:
                    label = shape['label']
                    if label not in classes:
                        continue
                    
                    class_id = classes.index(label)
                    
                    # Handle polygon shapes by finding min/max coordinates
                    points = shape['points']
                    x_min = min(p[0] for p in points)
                    y_min = min(p[1] for p in points)
                    x_max = max(p[0] for p in points)
                    y_max = max(p[1] for p in points)
                    
                    # Convert to YOLO format (normalized)
                    x_center = (x_min + x_max) / 2 / image_width
                    y_center = (y_min + y_max) / 2 / image_height
                    width = (x_max - x_min) / image_width
                    height = (y_max - y_min) / image_height
                    
                    yolo_annotations.append(f"{class_id} {x_center} {y_center} {width} {height}")
                
                # Save to YOLO format file
                output_file = os.path.join(output_path, filename.replace(".json", ".txt"))
                with open(output_file, 'w') as out_file:
                    out_file.write("\n".join(yolo_annotations))

# Example usage
classes = ["Car", "Road", "Sign", "People"]  # List of classes
labelme_to_yolo(r"C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\annotations_val", r"C:\Users\janmi\PycharmProjects\road_detection_model\road_detection_model\datasets\labels\valids", classes)


Dodanie kolejnych zdjęć do datasetu. Sprawdzenie indeksów i wymiarów zdjęć i zmienienie rozszerzenia z .png na .jpg

In [5]:
import os

# Path to the directory containing the images
directory = r'C:\Users\janmi\OneDrive\Pulpit\data'

# Starting index
start_index = 1425

# Get a list of all files in the directory
files = sorted(os.listdir(directory))

# Check if the number of files is correct
for idx, filename in enumerate(files):
    # Ensure the file has the correct extension before processing
    if filename.lower().endswith('.jpg'):
        # Construct the new filename with 10 digits and change extension to .jpg
        new_filename = f"{start_index + idx:010d}.png"
        
        # Get the full path of the old and new filenames
        old_file = os.path.join(directory, filename)
        new_file = os.path.join(directory, new_filename)
        
        # Rename the file
        os.rename(old_file, new_file)

print("File renaming and extension change completed successfully.")


File renaming and extension change completed successfully.


In [4]:
import os
from PIL import Image

# Path to the directory containing the images
directory = r'C:\Users\janmi\OneDrive\Pulpit\test\S00044'

# Desired size
new_size = (1392, 512)

# Starting index for renaming
start_index = 1425

# Get a list of all files in the directory
files = sorted(os.listdir(directory))

# Check if the number of files is correct
for idx, filename in enumerate(files):
    # Full path to the original file
    old_file = os.path.join(directory, filename)
    
    # Check if the file is a jpg
    if filename.lower().endswith('.jpg'):
        # Open the image
        with Image.open(old_file) as img:
            # Resize the image
            img = img.resize(new_size, Image.LANCZOS)
            
            # Construct the new filename with 10 digits and .png extension
            new_filename = f"{start_index + idx:010d}.png"
            
            # Full path to the new file
            new_file = os.path.join(directory, new_filename)
            
            # Save the image as PNG
            img.save(new_file, 'PNG')
            
print("Image resizing and format conversion completed successfully.")


Image resizing and format conversion completed successfully.


In [1]:
!python C:\Users\janmi\PycharmProjects\Magisterka\yolov5\train.py --img 640 --batch 16 --epochs 100 --data C:\Users\janmi\PycharmProjects\Magisterka\yolov5\car_dataset.yaml --weights C:\Users\janmi\PycharmProjects\Magisterka\yolov5\yolov5x.pt

Using device: cuda:0


IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [2]:
!python C:\Users\janmi\PycharmProjects\Magisterka\yolov5\detect.py --weights C:\Users\janmi\PycharmProjects\Magisterka\yolov5\runs\train\exp6\weights\best.pt --img 640 --conf 0.25 --source C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\test

detect: weights=['C:\\Users\\janmi\\PycharmProjects\\Magisterka\\yolov5\\runs\\train\\exp6\\weights\\best.pt'], source=C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\test, data=yolov5\data\coco128.yaml, imgsz=[640, 640], conf_thres=0.25, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=False, save_csv=False, save_conf=False, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=yolov5\runs\detect, name=exp, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False, vid_stride=1
YOLOv5  v7.0-331-gab364c98 Python-3.12.4 torch-2.3.1+cu121 CUDA:0 (NVIDIA GeForce RTX 4060 Ti, 8188MiB)

Fusing layers... 
Model summary: 322 layers, 86193601 parameters, 0 gradients, 203.8 GFLOPs
image 1/634 C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\test\0000000000.png: 256x640 1 car, 1 road, 1 sign, 47.0ms
image 2/634 C:\Users\janmi\PycharmProjects\Magisterka\yolov5\images\te

Try another approach: